In [1]:
import numpy as np
from scipy.linalg import expm, sinm, cosm
import pandas as pd
import matplotlib.pyplot as plt
import statsmodels.api as sm
import math
from scipy.special import iv
from statsmodels.tsa.arima.model import ARIMA
import altair

In [2]:
def mets_filter(ts,rho,alpha):
    ts_mean = np.mean(ts)
    ts = np.append(ts,ts_mean)
    sample_size = len(ts)
    
    L_approx = np.zeros([sample_size, sample_size])

    for row in range(0,len(L_approx)-1):
        L_approx[row][row+1] =1

    L_approx[sample_size -1 ] = np.zeros(sample_size)
    filter_matrix = expm(rho*L_approx)
    
    output = np.dot(filter_matrix,ts) + alpha

    return output[:-1]


def ols_mets(ts, grid_size):
    sample_size = len(ts)
    L_approx = np.zeros([sample_size, sample_size])

    for row in range(0,len(L_approx)-1):
        L_approx[row][row+1] =1
    
    min_rho =  0.0
    filter_matrix = expm(min_rho*L_approx)
    resid = np.dot(filter_matrix,ts)
    min_alpha =  np.mean(resid)
    min_obj = np.square(np.std(resid))
    
    for rho in np.linspace(-2,2,grid_size):
        filter_matrix = expm(rho*L_approx)
        resid =  np.dot(filter_matrix,ts)
        alpha =  np.mean(resid)
        obj = np.square(np.std(resid))
        
        if obj < min_obj:
            min_alpha = alpha
            min_rho = rho
            min_obj = obj

    return [min_alpha, min_rho, min_obj]    

# Annual Data

In [3]:
m3_df = pd.read_excel( 'C:/Users/michelj8/Documents/GitHub/exp_smooth_lasso/m3_data.xls', sheet_name = 'M3Year')
m3_df.head()

Series   N  NF      Category  Starting Year  Unnamed: 5        1        2  \
0  N   1  20   6  MICRO                  1975           1   940.66  1084.86   
1  N   2  20   6  MICRO                  1975           1  1991.05  2306.40   
2  N   3  20   6  MICRO                  1975           1  1461.57  1692.50   
3  N   4  20   6  MICRO                  1975           1   744.54  1105.16   
4  N   5  20   6  MICRO                  1975           1  4977.18  5248.00   

         3        4  ...  38  39  40  41  42  43  44  45  46  47  
0  1244.98  1445.02  ... NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN  
1  2604.00  2992.30  ... NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN  
2  2193.82  2459.68  ... NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN  
3  1417.40  1838.04  ... NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN  
4  5370.00  6184.89  ... NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN  

[5 rows x 53 columns]

In [4]:
ar_mse = []
mets_mse  = []
series_type = []

ar_coef = []
mets_coef = []

for index in m3_df.index:
# for index in range(0, 10):
    series_type.append( m3_df.loc[index,'Category'] )
    ts = m3_df.drop(columns = ['Series','N','NF','Category', 'Starting Year','Unnamed: 5']).loc[index].dropna()
    ts = ts.diff(1).dropna().values
    mets_model = ols_mets(ts, 50)
    mets_mse.append(mets_model[2] )
    mets_coef.append(-1*mets_model[1])
    
    ar_model = ARIMA(ts,order = (1,0,0)).fit()
    ar_mse.append(np.mean(np.square(ts- ar_model.predict())))
    ar_coef.append(ar_model.params[1])

C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:963: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'


In [5]:
yearly_est_df = pd.DataFrame({'mets_mse':mets_mse, 
                              'ar_mse':ar_mse,
                              'series_type':series_type,
                             'ar_coef':ar_coef,
                             'mets_coef':mets_coef})

yearly_est_df['MSE_Ratio'] =  100*(yearly_est_df['mets_mse']-yearly_est_df['ar_mse'])/yearly_est_df['ar_mse']
yearly_est_df['mets_beats_ar'] = 1*(yearly_est_df['MSE_Ratio'] < 0)
yearly_est_df.head()

mets_mse         ar_mse   series_type   ar_coef  mets_coef  MSE_Ratio  \
0   43810.073092   28149.950060  MICRO         0.756800   0.448980  55.631086   
1  393612.297666  393259.580735  MICRO         0.191862   0.204082   0.089691   
2  333659.054204  332617.127877  MICRO         0.337169   0.367347   0.313251   
3  367866.853314  368491.054723  MICRO         0.034072   0.040816  -0.169394   
4  480823.548746  480701.033278  MICRO         0.017069   0.040816   0.025487   

   mets_beats_ar  
0              0  
1              0  
2              0  
3              1  
4              0

In [6]:
print (100*yearly_est_df['mets_beats_ar'].mean())
print()
yearly_est_df[['mets_beats_ar','series_type']].groupby('series_type').mean().multiply(100).apply(lambda s: round(s,1))

57.984496124031004



mets_beats_ar
series_type                
DEMOGRAPHIC            51.8
FINANCE                58.6
INDUSTRY               59.8
MACRO                  73.5
MICRO                  54.8
OTHER                 100.0

In [7]:
(altair.Chart(yearly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR(1) Coefficient'),
         y=altair.Y('mets_coef',title = 'METS Coefficient'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [8]:
(altair.Chart(yearly_est_df).mark_bar().encode(
    altair.X("MSE_Ratio", bin=True, title = 'Normalized difference in MSE'),
    y='count()')
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [9]:
(altair.Chart(yearly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('mets_coef', title = 'METS Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [10]:
(altair.Chart(yearly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

# Quarterly

In [30]:
m3_df = pd.read_excel( 'C:/Users/michelj8/Documents/GitHub/exp_smooth_lasso/m3_data.xls', sheet_name = 'M3Quart')

ar_mse = []
mets_mse  = []
series_type = []

ar_coef = []
mets_coef = []

for index in m3_df.index:
# for index in range(0, 10):
    ts = m3_df.drop(columns = ['Series','N','NF','Category', 'Starting Year','Starting Quarter']).loc[index].dropna()
    series_type.append( m3_df.loc[index,'Category'] )
    ts = ts.diff(1).dropna().values
    mets_model = ols_mets(ts, 50)
    mets_mse.append(mets_model[2] )
    mets_coef.append(-1*mets_model[1])
    
    ar_model = ARIMA(ts,order = (1,0,0)).fit()
    ar_mse.append(np.mean(np.square(ts- ar_model.predict())))
    ar_coef.append(ar_model.params[1])
    

quarterly_est_df = pd.DataFrame({'mets_mse':mets_mse, 
                              'ar_mse':ar_mse,
                              'series_type':series_type,
                             'ar_coef':ar_coef,
                             'mets_coef':mets_coef})

quarterly_est_df['MSE_Ratio'] =  100*(quarterly_est_df['mets_mse']-quarterly_est_df['ar_mse'])/quarterly_est_df['ar_mse']
quarterly_est_df['mets_beats_ar'] = 1*(quarterly_est_df['MSE_Ratio'] < 0)
quarterly_est_df.head()

C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:963: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'


mets_mse        ar_mse   series_type   ar_coef  mets_coef  MSE_Ratio  \
0  64264.409861  64217.156127  MICRO         0.027433  -0.000000   0.073584   
1   4630.309766   4561.081330  MICRO        -0.208103  -0.122449   1.517808   
2  23137.541167  23178.527449  MICRO         0.012556   0.040816  -0.176829   
3  97532.764107  96721.799399  MICRO        -0.169962  -0.122449   0.838451   
4  15398.379995  13608.294346  MICRO         0.617972   0.530612  13.154372   

   mets_beats_ar  
0              0  
1              0  
2              1  
3              0  
4              0

In [12]:
print (100*quarterly_est_df['mets_beats_ar'].mean())
print()
quarterly_est_df[['mets_beats_ar','series_type']].groupby('series_type').mean().multiply(100).apply(lambda s: round(s,1))

61.111111111111114



mets_beats_ar
series_type                 
DEMOGRAPHIC             61.4
FINANCE                 61.8
INDUSTRY                79.5
MACRO                   52.1
MICRO                   68.1

In [13]:
(altair.Chart(quarterly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR(1) Coefficient'),
         y=altair.Y('mets_coef',title = 'METS Coefficient'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [14]:
(altair.Chart(quarterly_est_df).mark_bar().encode(
    altair.X("MSE_Ratio", bin=True, title = 'Normalized difference in MSE'),
    y='count()')
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [15]:
(altair.Chart(quarterly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('mets_coef', title = 'METS Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [16]:
(altair.Chart(quarterly_est_df, title = 'Quarterly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

# Monthly

In [17]:
m3_df = pd.read_excel( 'C:/Users/michelj8/Documents/GitHub/exp_smooth_lasso/m3_data.xls', sheet_name = 'M3Month')

ar_mse = []
mets_mse  = []
series_type = []

ar_coef = []
mets_coef = []

for index in m3_df.index:
# for index in range(0, 50):
    ts = m3_df.drop(columns = ['Series','N','NF','Category', 'Starting Year','Starting Month']).loc[index].dropna()
    series_type.append( m3_df.loc[index,'Category'] )
    ts = np.log(ts).diff(1).dropna().values
    mets_model = ols_mets(ts, 50)
    mets_mse.append(mets_model[2] )
    mets_coef.append(-1*mets_model[1])
    
    ar_model = ARIMA(ts,order = (1,0,0)).fit()
    ar_mse.append(np.mean(np.square(ts- ar_model.predict())))
    ar_coef.append(ar_model.params[1])
    

monthly_est_df = pd.DataFrame({'mets_mse':mets_mse, 
                              'ar_mse':ar_mse,
                              'series_type':series_type,
                             'ar_coef':ar_coef,
                             'mets_coef':mets_coef})

monthly_est_df['MSE_Ratio'] =  100*(monthly_est_df['mets_mse']-monthly_est_df['ar_mse'])/monthly_est_df['ar_mse']
monthly_est_df['mets_beats_ar'] = 1*(monthly_est_df['MSE_Ratio'] < 0)
monthly_est_df.head()

C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\base\model.py:567: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warn("Maximum Likelihood optimization failed to converge. "
C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\base\model.py:567: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warn("Maximum Likelihood optimization failed to converge. "
C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\base\model.py:567: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warn("Maximum Likelihood optimization failed to converge. "
C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\base\model.py:567: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warn("Maximum Likelihood optimization failed to converge. "
C:\Users\michelj8\Anaconda3\lib\site-packages\statsmodels\base\model.py:567: Converg

mets_mse    ar_mse   series_type   ar_coef  mets_coef  MSE_Ratio  \
0  0.504835  0.651061  MICRO        -0.518105  -1.020408 -22.459644   
1  0.869515  0.975221  MICRO        -0.505090  -0.775510 -10.839131   
2  0.241218  0.271305  MICRO        -0.515090  -0.775510 -11.089740   
3  0.517072  0.626328  MICRO        -0.560277  -0.938776 -17.443952   
4  0.296919  0.362953  MICRO        -0.529051  -0.938776 -18.193551   

   mets_beats_ar  
0              1  
1              1  
2              1  
3              1  
4              1

In [18]:
print (100*monthly_est_df['mets_beats_ar'].mean())
print()
monthly_est_df[['mets_beats_ar','series_type']].groupby('series_type').mean().multiply(100).apply(lambda s: round(s,1))

75.28011204481793



mets_beats_ar
series_type                
DEMOGRAPHIC            37.8
FINANCE                68.3
INDUSTRY               79.6
MACRO                  61.9
MICRO                  96.8
OTHER                  30.8

In [19]:
(altair.Chart(monthly_est_df, title = 'Monthly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR(1) Coefficient'),
         y=altair.Y('mets_coef',title = 'METS Coefficient'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [20]:
(altair.Chart(monthly_est_df).mark_bar().encode(
    altair.X("MSE_Ratio", bin=True, title = 'Normalized difference in MSE'),
    y='count()')
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [21]:
(altair.Chart(monthly_est_df, title = 'Monthly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('mets_coef', title = 'METS Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

In [22]:
(altair.Chart(monthly_est_df, title = 'Monthly M3 Estimation')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'))
#          color=altair.Color('series_type', title = 'Series Type') )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Series Type'),
    columns=3
)
)

alt.FacetChart(...)

# Combination Graphs

In [31]:
yearly_est_df['freq'] = 'yearly'
quarterly_est_df['freq'] = 'quarterly'
monthly_est_df['freq'] = 'monthly'

frames = [yearly_est_df, quarterly_est_df, monthly_est_df]
total_df = result = pd.concat(frames)
total_df.loc[total_df['series_type'] ==  total_df['series_type'].unique()[4],'series_type'] = total_df['series_type'].unique()[6]

In [32]:
round(100*total_df['mets_beats_ar'].mean(),1)

67.7

In [33]:
total_df[['series_type','mets_beats_ar']].groupby('series_type').mean().apply(lambda s: round(100.0*s,1))

mets_beats_ar
series_type                 
DEMOGRAPHIC             49.4
FINANCE                 67.0
INDUSTRY                75.7
MACRO                   58.5
MICRO                   82.2
OTHER                   42.9

In [34]:
total_df[['freq','mets_beats_ar']].groupby('freq').mean().apply(lambda s: round(100.0*s,1))

mets_beats_ar
freq                    
monthly             75.3
quarterly           61.8
yearly              58.0

In [35]:
pd.pivot_table( total_df[['series_type','mets_beats_ar','freq']].groupby(['series_type','freq']).mean().reset_index(),
               columns = 'freq',
               index = 'series_type',
               values = 'mets_beats_ar').apply(lambda s: round(100.0*s,1))

freq           monthly  quarterly  yearly
series_type                              
DEMOGRAPHIC       37.8       61.4    51.8
FINANCE           68.3       71.1    58.6
INDUSTRY          79.6       79.5    59.8
MACRO             61.9       51.8    73.5
MICRO             96.8       67.6    54.8
OTHER             30.8        NaN   100.0

In [36]:
(altair.Chart(total_df, title = 'Coefficients')
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR(1) Coefficient'),
         y=altair.Y('mets_coef',title = 'METS Coefficient'),
         color=altair.Color('freq', title = 'Data Frequency', scale=altair.Scale(scheme='redyellowblue')) )
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Estimated coefficients across series and frequency'),
    columns=3
)
)

alt.FacetChart(...)

In [37]:
(altair.Chart(total_df).mark_bar().encode(
    altair.X("MSE_Ratio", bin=altair.Bin(extent=[-30, 30], step=10), title = 'Normalized difference in MSE'),
    y='count()',
    color = altair.Color('freq', title = 'Data Frequency'))
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Comparison of MSE across series type and frequency'),
    columns=3
)
)

alt.FacetChart(...)

In [41]:
(altair.Chart(total_df.query('MSE_Ratio < 100'))
 .mark_point()
 .encode(x=altair.X('mets_coef', title = 'METS Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'),
    color = altair.Color('freq', title = 'Data Frequency'))
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Comparison of AR and METS coefficient'),
    columns=3
)
)

alt.FacetChart(...)

In [43]:
(altair.Chart(total_df.query('MSE_Ratio < 100'))
 .mark_point()
 .encode(x=altair.X('ar_coef', title = 'AR Coefficient'),
         y=altair.Y('MSE_Ratio',title = 'Normalized difference in MSE'),
    color = altair.Color('freq', title = 'Data Frequency'))
 .properties(
    width=180,
    height=180)
.facet(
    facet=altair.Facet('series_type', title = 'Comparison of AR and METS coefficient'),
    columns=3
)
)

alt.FacetChart(...)

In [44]:
total_df

mets_mse         ar_mse   series_type   ar_coef  mets_coef  \
0      43810.073092   28149.950060  MICRO         0.756800   0.448980   
1     393612.297666  393259.580735  MICRO         0.191862   0.204082   
2     333659.054204  332617.127877  MICRO         0.337169   0.367347   
3     367866.853314  368491.054723  MICRO         0.034072   0.040816   
4     480823.548746  480701.033278  MICRO         0.017069   0.040816   
...             ...            ...           ...       ...        ...   
1423       0.000077       0.000077  OTHER        -0.158897  -0.122449   
1424       0.000135       0.000135  OTHER        -0.058612  -0.040816   
1425       0.000112       0.000112  OTHER         0.043298   0.040816   
1426       0.000053       0.000053  OTHER         0.124879   0.122449   
1427       0.000117       0.000117  OTHER        -0.196147  -0.204082   

      MSE_Ratio  mets_beats_ar     freq  
0     55.631086              0   yearly  
1      0.089691              0   yearly  
2      0.313251              0   yearly  
3     -0.169394              1   yearly  
4      0.025487              0   yearly  
...         ...            ...      ...  
1423   0.107945              0  monthly  
1424   0.029974              0  monthly  
1425  -0.153085              1  monthly  
1426   0.298193              0  monthly  
1427  -0.350882              1  monthly  

[2829 rows x 8 columns]